## Preparing environment

In [ ]:
%pip install tritonclient[http]

In [ ]:
import json
import numpy as np
import os
import requests
import sys
import time
import tensorflow as tf
import tritonclient.http as httpclient

from PIL import Image
from tritonclient.utils import InferenceServerException


%matplotlib inline
%state_exclude triton_client # triton_client is non-serialized variable so let's turn off the warning

In [ ]:
def create_tensor(image):
    image = image.resize((300, 300))
    (im_width, im_height) = image.size
    return np.asarray(image).reshape((1, im_height, im_width, 3)).astype(np.uint8)
    
    return image_tensor


In [ ]:
# load sample image
image_url = 'https://github.com/tensorflow/models/raw/master/research/object_detection/test_images/image2.jpg'
image = Image.open(requests.get(image_url, stream=True).raw)

image_tensor = create_tensor(image)

## Authentication

In [ ]:
headers = {
    "Authorization": f"Bearer {os.environ['iam-token']}", # get IAM token from secrets
    "x-node-id": "bt1hpm3u72cbnipfcm0i",  # sample node
    "x-folder-id": "b1g4bh24c406i24vsomt" # node folder ID
}

# models built in Docker image with Triton Inference Server
models = [
    'resnet152_640x640',
    'inception_resnet_v2_640x640'
]

## Test requests

In [ ]:
# construct the client with DataSphere Node API address
triton_client = httpclient.InferenceServerClient(url="node-api.datasphere.yandexcloud.net", ssl=True)

# prepare sample payload
payload = httpclient.InferInput("input_tensor", list(image_tensor.shape), "UINT8")
payload.set_data_from_numpy(image_tensor, binary_data=False)

In [ ]:
# execute inference with different models
model = models[0]
print(f"Inferring with {model}")
results = triton_client.infer(model, inputs=[payload], headers=headers)   
results.get_response()

In [ ]:
# execute inference with different models
model = models[1]
print(f"Inferring with {model}")
results = triton_client.infer(model, inputs=[payload], headers=headers)
results.get_response()